# (Practicing) Making Road Network by python

* This code is based on tutorial which is written by JUNPYO PARK
    * Tutorial URL : https://junpyopark.github.io/road-network-construction-1/
    * Github code URL : https://github.com/JunPyoPark/Networkx-Projects

In [20]:
# import Libraries

import shapefile
import pandas as pd
from pyproj import Proj, transform
import os
import folium
import networkx as nx
import numpy as np

In [3]:
#read data as pandas dataframe

shp_path_node = './nodelinks/MOCT_NODE.shp'
shp_path_link = './nodelinks/MOCT_LINK.shp'

sf_node = shapefile.Reader(shp_path_node)
sf_link = shapefile.Reader(shp_path_link)

fields_node = [x[0] for x in sf_node.fields][1:]
records_node = sf_node.records()
shps = [s.points for s in sf_node.shapes()]
fields_link = [x[0] for x in sf_link.fields][1:]
records_link = sf_link.records()

node_dataframe = pd.DataFrame(columns=fields_node, data=records_node)
node_dataframe = node_dataframe.assign(coords=shps)
link_dataframe = pd.DataFrame(columns=fields_link, data=records_link)

In [4]:
node_dataframe[1:5]

NODE_ID NODE_TYPE                                    NODE_NAME TURN_P  \
1  3330016500       104          b'\xb9\xfa\xb1\xb3\xc5\xcd\xb3\xce'      0   
2  3330015600       104          b'\xb9\xfa\xb1\xb3\xc5\xcd\xb3\xce'      0   
3  3330014900       101  b'\xb9\xfa\xb1\xb3\xb1\xb3\xc2\xf7\xb7\xce'      0   
4  3330014600       101  b'\xb9\xfa\xb1\xb3\xb1\xb3\xc2\xf7\xb7\xce'      0   

  REMARK USER_ID WORKSTATE DEPT_CODE STNL_REG           TMPID UPLOAD_ID  \
1          korea         5                333  OEXT3330016500             
2          korea         5                333  OEXT3330015600             
3          korea         5                333  OEXT3330014900             
4          korea         5                333  OEXT3330014600             

                                       coords  
1  [[229535.21800000034, 250194.52040000074]]  
2  [[229465.27020000014, 249416.52300000004]]  
3  [[229455.64099999983, 249249.00129999965]]  
4  [[229412.60429999977, 249169.92640000023]]

In [5]:
df_node = pd.DataFrame()
df_link = pd.DataFrame()
for ii in range(100,124):
    res_node = node_dataframe[node_dataframe['STNL_REG'] == str(ii) ] # STNL_REG is not int.
    res_link = link_dataframe[link_dataframe['STNL_REG'] == str(ii) ]
    df_node = pd.concat([df_node,res_node],ignore_index=True) # marge data
    df_link = pd.concat([df_link,res_link],ignore_index=True)

In [6]:
df_node[1:5]

NODE_ID NODE_TYPE                                          NODE_NAME  \
1  1000017800       101        b'\xc6\xc4\xc5\xa9\xba\xe4\xc5\xb8\xbf\xf6'   
2  1000018000       101  b'\xc0\xfb\xbc\xb1\xc7\xf6\xb4\xeb\xba\xf4\xb5...   
3  1000007300       101  b'\xbc\xbc\xc1\xbe\xb7\xce\xbb\xe7\xb0\xc5\xb8...   
4  1000007600       101  b'\xbc\xbc\xc1\xbe\xb7\xce\xbb\xe7\xb0\xc5\xb8...   

  TURN_P REMARK USER_ID WORKSTATE DEPT_CODE STNL_REG TMPID UPLOAD_ID  \
1      1                        5     11110      100                   
2      1                        5     11110      100                   
3      0                        5     11110      100                   
4      0                        5     11110      100                   

                                      coords  
1  [[197248.12399999984, 552890.1248000003]]  
2   [[197587.4173999997, 552862.0014999993]]  
3   [[197963.9944000002, 552227.1275999993]]  
4  [[197897.61730000004, 552286.2988000009]]

In [7]:
for idx,row in df_node.iterrows():
    if type(row['NODE_NAME']) == bytes :
        # row['NODE_NAME'] = row['NODE_NAME'].decode('euc_kr')
        row['NODE_NAME'] = row['NODE_NAME'].decode('cp949')

In [8]:
df_node[1:5]

NODE_ID NODE_TYPE     NODE_NAME TURN_P REMARK USER_ID WORKSTATE  \
1  1000017800       101         파크뷰타워      1                        5   
2  1000018000       101        적선현대빌딩      1                        5   
3  1000007300       101  세종로사거리_태평로_진      0                        5   
4  1000007600       101  세종로사거리_일반국도6      0                        5   

  DEPT_CODE STNL_REG TMPID UPLOAD_ID  \
1     11110      100                   
2     11110      100                   
3     11110      100                   
4     11110      100                   

                                      coords  
1  [[197248.12399999984, 552890.1248000003]]  
2   [[197587.4173999997, 552862.0014999993]]  
3   [[197963.9944000002, 552227.1275999993]]  
4  [[197897.61730000004, 552286.2988000009]]

In [9]:
inProj = Proj(init = 'epsg:5186')
outProj= Proj(init = 'epsg:4326')
latitude = []
longitude= []
for idx,row in df_node.iterrows():
    x,y  = row.coords[0][0],row.coords[0][1]  # korea 2000 좌표계
    nx,ny = transform(inProj,outProj,x,y)     # 새로운 좌표계    
    latitude.append(ny)
    longitude.append(nx)
df_node['latitude'] = latitude
df_node['longitude']= longitude
del df_node['coords'] # delete coords

In [10]:
df_node[1:5]

NODE_ID NODE_TYPE     NODE_NAME TURN_P REMARK USER_ID WORKSTATE  \
1  1000017800       101         파크뷰타워      1                        5   
2  1000018000       101        적선현대빌딩      1                        5   
3  1000007300       101  세종로사거리_태평로_진      0                        5   
4  1000007600       101  세종로사거리_일반국도6      0                        5   

  DEPT_CODE STNL_REG TMPID UPLOAD_ID   latitude   longitude  
1     11110      100                  37.575554  126.968848  
2     11110      100                  37.575301  126.972689  
3     11110      100                  37.569582  126.976953  
4     11110      100                  37.570115  126.976202

In [11]:
df_node.rename(columns={'NODE_ID':'Id'},inplace = True)
df_link.rename(columns={'F_NODE':'Source','T_NODE':'Target'},inplace = True)

In [13]:
# save dataframe as csv
df_node.to_csv('seoul_nodes_181002.csv') # node list
df_link.to_csv('seoul_links_181002.csv') # edge(=link) list

In [9]:
nodes = pd.read_csv('./seoul_nodes_181002.csv')
links = pd.read_csv('./seoul_links_181002.csv')

In [10]:
nodes[1:5]

Unnamed: 0          Id  NODE_TYPE     NODE_NAME  TURN_P REMARK USER_ID  \
1           1  1000017800        101         파크뷰타워       1    NaN     NaN   
2           2  1000018000        101        적선현대빌딩       1    NaN     NaN   
3           3  1000007300        101  세종로사거리_태평로_진       0    NaN     NaN   
4           4  1000007600        101  세종로사거리_일반국도6       0    NaN     NaN   

   WORKSTATE  DEPT_CODE  STNL_REG TMPID UPLOAD_ID   latitude   longitude  
1          5      11110       100   NaN       NaN  37.575554  126.968848  
2          5      11110       100   NaN       NaN  37.575301  126.972689  
3          5      11110       100   NaN       NaN  37.569582  126.976953  
4          5      11110       100   NaN       NaN  37.570115  126.976202

In [11]:
nodes = nodes[['Id','NODE_NAME','latitude','longitude']]

In [14]:
links = links[['Source','Target']]

In [17]:
source_in = links['Source'].apply(lambda x : x in list(nodes['Id']))
target_in = links['Target'].apply(lambda x : x in list(nodes['Id']))
seoul_links = links[source_in & target_in] # contain if both target and source are contained in incheon_id

In [21]:
G = nx.Graph()
# R is the Earth's radius
R = 6371e3

for idx,row in nodes.iterrows():
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in seoul_links.iterrows():
    ## Calculate the distance between Source and Target Nodes
    lon1 = float(nodes[nodes['Id'] == row['Source']]['longitude'] * np.pi/180)
    lat1 = float(nodes[nodes['Id'] == row['Source']]['latitude'] * np.pi/180)
    lon2 = float(nodes[nodes['Id'] == row['Target']]['longitude'] * np.pi/180)
    lat2 = float(nodes[nodes['Id'] == row['Target']]['latitude'] * np.pi/180)
    d_lat = lat2 - lat1
    d_lon = lon2 - lon1
    a = np.sin(d_lat/2) ** 2 + np.cos(lat1) * np.cos(lat2) * np.sin(d_lon/2) ** 2
    c = 2 * np.arctan2(a**0.5, (1-a) ** 0.5)
    d = R * c
    
    G.add_edge(row['Source'],row['Target'],weight = d)

In [22]:
print(nx.info(G))

Name: 
Type: Graph
Number of nodes: 7405
Number of edges: 11923
Average degree:   3.2203


In [30]:
std_point = [37.566047, 126.977702]
std_point

[37.566047, 126.977702]

In [38]:
map_osm = folium.Map(location=[37.566047, 126.977702], zoom_start=10) 
for ix, row in nodes.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=G.degree[row['Id']] * 10, # 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='red',
        fill=True, 
    ).add_to(map_osm)
map_osm

In [39]:
map_osm.save("my_map.html") 